In [10]:
!pip install pydub mutagen pytaglib

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 KB 2.1 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 894.4/894.4 KB 4.0 MB/s eta 0:00:0000:0100:01


In [19]:
from pydub import AudioSegment
from pydub.utils import mediainfo
import taglib
import os

def make_mono(in_file, out_file):
    sound = AudioSegment.from_wav(in_file)
    sound = sound.set_channels(1)
    tags = mediainfo(in_file).get('TAG', {})
    tags['TRACKNUMBER'] = tags['track']
    print(in_file)
    sound.export(out_file, format="wav")
    with taglib.File(out_file, save_on_exit=True) as song:
        song.tags = tags
    print(mediainfo(out_file))

for file in os.listdir('../seth/wavs'):
    make_mono("../seth/wavs/"+file, "../sethmono/wavs/"+file)

../seth/wavs/SK001-0001.wav
{'index': '0', 'codec_name': 'pcm_s16le', 'codec_long_name': 'PCM signed 16-bit little-endian', 'profile': 'unknown', 'codec_type': 'audio', 'codec_tag_string': '[1][0][0][0]', 'codec_tag': '0x0001', 'sample_fmt': 's16', 'sample_rate': '22050', 'channels': '1', 'channel_layout': 'unknown', 'bits_per_sample': '16', 'id': 'N/A', 'r_frame_rate': '0/0', 'avg_frame_rate': '0/0', 'time_base': '1/22050', 'start_pts': 'N/A', 'start_time': 'N/A', 'duration_ts': '169216', 'duration': '7.674195', 'bit_rate': '354171', 'max_bit_rate': 'N/A', 'bits_per_raw_sample': 'N/A', 'nb_frames': 'N/A', 'nb_read_frames': 'N/A', 'nb_read_packets': 'N/A', 'DISPOSITION': {'default': '0', 'dub': '0', 'original': '0', 'comment': '0', 'lyrics': '0', 'karaoke': '0', 'forced': '0', 'hearing_impaired': '0', 'visual_impaired': '0', 'clean_effects': '0', 'attached_pic': '0', 'timed_thumbnails': '0'}, 'filename': '../sethmono/wavs/SK001-0001.wav', 'nb_streams': '1', 'nb_programs': '0', 'format_

In [20]:
import os

# Trainer: Where the ✨️ happens.
# TrainingArgs: Defines the set of arguments of the Trainer.
from trainer import Trainer, TrainerArgs

# GlowTTSConfig: all model related values for training, validating and testing.
from TTS.tts.configs.vits_config import VitsConfig

# BaseDatasetConfig: defines name, formatter and path of the dataset.
from TTS.tts.configs.shared_configs import BaseDatasetConfig
from TTS.tts.datasets import load_tts_samples
from TTS.tts.models.vits import Vits
from TTS.tts.utils.text.tokenizer import TTSTokenizer
from TTS.utils.audio import AudioProcessor

# we use the same path as this script as our training folder.
output_path = os.path.dirname(os.path.abspath('../../TTS'))

# DEFINE DATASET CONFIG
# Set LJSpeech as our target dataset and define its path.
# You can also use a simple Dict to define the dataset and pass it to your custom formatter.
dataset_config = BaseDatasetConfig(
    formatter="ljspeech", meta_file_train="metadata.csv", path=os.path.join(output_path, "SethVoice/sethmono")
)

# INITIALIZE THE TRAINING CONFIGURATION
# Configure the model. Every config class inherits the BaseTTSConfig.
config = VitsConfig(
    datasets=[dataset_config],
)

# INITIALIZE THE AUDIO PROCESSOR
# Audio processor is used for feature extraction and audio I/O.
# It mainly serves to the dataloader and the training loggers.
ap = AudioProcessor.init_from_config(config)

# INITIALIZE THE TOKENIZER
# Tokenizer is used to convert text to sequences of token IDs.
# If characters are not defined in the config, default characters are passed to the config
tokenizer, config = TTSTokenizer.init_from_config(config)

# LOAD DATA SAMPLES
# Each sample is a list of ```[text, audio_file_path, speaker_name]```
# You can define your custom sample loader returning the list of samples.
# Or define your custom formatter and pass it to the `load_tts_samples`.
# Check `TTS.tts.datasets.load_tts_samples` for more details.
train_samples, eval_samples = load_tts_samples(
    dataset_config,
    eval_split=True,
    eval_split_max_size=config.eval_split_max_size,
    eval_split_size=config.eval_split_size,
)

# INITIALIZE THE MODEL
# Models take a config object and a speaker manager as input
# Config defines the details of the model like the number of layers, the size of the embedding, etc.
# Speaker manager is used by multi-speaker models.
model = Vits(config, ap, tokenizer, speaker_manager=None)

# INITIALIZE THE TRAINER
# Trainer provides a generic API to train all the 🐸TTS models with all its perks like mixed-precision training,
# distributed training, etc.
trainer = Trainer(
    TrainerArgs(), config, output_path, model=model, train_samples=train_samples, eval_samples=eval_samples
)

# AND... 3,2,1... 🚀
trainer.fit()

 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 | > Found 685 files in /root/tts-output/SethVoice/sethmono


 > Training Environment:
 | > Backend: Torch
 | > Mixed precision: False
 | > Precision: float32
 | > Current device: 0
 | > Num. of GPUs: 1
 | > Num. of CPUs: 24
 | > Num. of Torch Threads: 12
 | > Torch seed: 54321
 | > Torch CUDNN: True
 | > Torch CUDNN deterministic: False
 | > Torch CUDNN benchmark: False
 | > Torch TF32 MatMul: False
 > Start Tensorboard: tensorboard --logdir=output/run-August-20-2023_07+53PM-0000000

 > Model has 83046892 parameters

 > EPOCH: 0/1000
 --> output/run-August-20-2023_07+53PM-0000000




> DataLoader initialization
| > Tokenizer:
	| > add_blank: True
	| > use_eos_bos: False
	| > use_phonemes: False
| > Number of instances : 679



 > TRAINING (2023-08-20 19:53:14) 


 | > Preprocessing samples
 | > Max text length: 172
 | > Min text length: 21
 | > Avg text length: 99.78350515463917
 | 
 | > Max audio length: 240538.0
 | > Min audio length: 35994.0
 | > Avg audio length: 136593.6406480118
 | > Num. instances discarded samples: 0
 | > Batch group size: 0.
eight. The press yard.

 [!] Character '\n' not found in the vocabulary. Discarding it.


...


  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.042020320892333984 (+0.0)
     | > avg_loss_disc: 2.5879015922546387 (+0.0)
     | > avg_loss_disc_real_0: 0.14270570874214172 (+0.0)
     | > avg_loss_disc_real_1: 0.24744370579719543 (+0.0)
     | > avg_loss_disc_real_2: 0.22576330602169037 (+0.0)
     | > avg_loss_disc_real_3: 0.2389000505208969 (+0.0)
     | > avg_loss_disc_real_4: 0.3522880971431732 (+0.0)
     | > avg_loss_disc_real_5: 0.2021651417016983 (+0.0)
     | > avg_loss_0: 2.5879015922546387 (+0.0)
     | > avg_loss_gen: 2.462860345840454 (+0.0)
     | > avg_loss_kl: 3.390918493270874 (+0.0)
     | > avg_loss_feat: 6.067783355712891 (+0.0)
     | > avg_loss_mel: 22.61332130432129 (+0.0)
     | > avg_loss_duration: 1.79788076877594 (+0.0)
     | > avg_loss_1: 36.332763671875 (+0.0)


 > EPOCH: 998/1000
 --> output/run-August-20-2023_07+53PM-0000000

 > TRAINING (2023-08-21 05:14:46) 

   --> TIME: 2023-08-21 05:15:13 -- STEP: 19/22 -- GLOBAL_STEP: 21975
     | > loss_dis

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.04080462455749512 (+0.0)
     | > avg_loss_disc: 2.878188371658325 (+0.0)
     | > avg_loss_disc_real_0: 0.5422994494438171 (+0.0)
     | > avg_loss_disc_real_1: 0.2109481245279312 (+0.0)
     | > avg_loss_disc_real_2: 0.2167869359254837 (+0.0)
     | > avg_loss_disc_real_3: 0.28374913334846497 (+0.0)
     | > avg_loss_disc_real_4: 0.1932520568370819 (+0.0)
     | > avg_loss_disc_real_5: 0.21001046895980835 (+0.0)
     | > avg_loss_0: 2.878188371658325 (+0.0)
     | > avg_loss_gen: 2.893807888031006 (+0.0)
     | > avg_loss_kl: 3.6630685329437256 (+0.0)
     | > avg_loss_feat: 7.070735931396484 (+0.0)
     | > avg_loss_mel: 24.164674758911133 (+0.0)
     | > avg_loss_duration: 1.8490735292434692 (+0.0)
     | > avg_loss_1: 39.641361236572266 (+0.0)


 > EPOCH: 999/1000
 --> output/run-August-20-2023_07+53PM-0000000

 > TRAINING (2023-08-21 05:15:19) 

 > EVALUATION 


  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.0457782745361328

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.04577827453613281 (+0.0)
     | > avg_loss_disc: 2.4534788131713867 (+0.0)
     | > avg_loss_disc_real_0: 0.23506343364715576 (+0.0)
     | > avg_loss_disc_real_1: 0.23500590026378632 (+0.0)
     | > avg_loss_disc_real_2: 0.21621599793434143 (+0.0)
     | > avg_loss_disc_real_3: 0.1838216930627823 (+0.0)
     | > avg_loss_disc_real_4: 0.21216070652008057 (+0.0)
     | > avg_loss_disc_real_5: 0.21108317375183105 (+0.0)
     | > avg_loss_0: 2.4534788131713867 (+0.0)
     | > avg_loss_gen: 2.5821428298950195 (+0.0)
     | > avg_loss_kl: 3.6322877407073975 (+0.0)
     | > avg_loss_feat: 6.899261951446533 (+0.0)
     | > avg_loss_mel: 23.964990615844727 (+0.0)
     | > avg_loss_duration: 1.9015870094299316 (+0.0)
     | > avg_loss_1: 38.98027038574219 (+0.0)



In [21]:
import os
os.path.exists('/root/tts-output/SethVoice/TTS/output/run-August-20-2023_07+53PM-0000000/config.json')

True

In [26]:
from TTS.api import Synthesizer

tts = Synthesizer(tts_checkpoint="../TTS/output/run-August-20-2023_07+53PM-0000000/checkpoint_20000.pth", tts_config_path="../TTS/output/run-August-20-2023_07+53PM-0000000/config.json")

#tts = TTS(model_name="/root/tts-output/run-July-26-2023_12+16AM-0000000/best_model_1908.pth", progress_bar=True, gpu=True)

 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024


In [29]:
outputs = tts.tts(text="Oh no, I have been kidnapped! April please pay the ransom so I can come home.")
tts.save_wav(outputs, "output.wav")

 > Text splitted to sentences.
['Oh no, I have been kidnapped!', 'April please pay the ransom so I can come home.']
 > Processing time: 0.9526216983795166
 > Real-time factor: 0.17988925432711309


In [ ]:
import os

from trainer import Trainer, TrainerArgs

from TTS.utils.audio import AudioProcessor
from TTS.vocoder.configs import HifiganConfig
from TTS.vocoder.datasets.preprocess import load_wav_data
from TTS.vocoder.models.gan import GAN

# we use the same path as this script as our training folder.
output_path = os.path.dirname(os.path.abspath('../../TTS'))

config = HifiganConfig(
    batch_size=32,
    eval_batch_size=16,
    num_loader_workers=4,
    num_eval_loader_workers=4,
    run_eval=True,
    test_delay_epochs=5,
    epochs=1000,
    seq_len=8192,
    pad_short=2000,
    use_noise_augment=True,
    eval_split_size=10,
    print_step=25,
    print_eval=False,
    mixed_precision=False,
    lr_gen=1e-4,
    lr_disc=1e-4,
    data_path= os.path.join(output_path, "SethVoice/sethmono/wavs"),
    output_path=output_path,
)

# init audio processor
ap = AudioProcessor(**config.audio.to_dict())

# load training samples
eval_samples, train_samples = load_wav_data(config.data_path, config.eval_split_size)

# init model
model = GAN(config, ap)

# init the trainer and 🚀
trainer = Trainer(
    TrainerArgs(), config, output_path, model=model, train_samples=train_samples, eval_samples=eval_samples
)
trainer.fit()

 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:-100
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:20
 | > fft_size:1024
 | > power:1.5
 | > preemphasis:0.0
 | > griffin_lim_iters:60
 | > signal_norm:True
 | > symmetric_norm:True
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:1.0
 | > pitch_fmax:640.0
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:4.0
 | > clip_norm:True
 | > do_trim_silence:True
 | > trim_db:45
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 > Generator Model: hifigan_generator
 > Discriminator Model: hifigan_discriminator


 > Training Environment:
 | > Backend: Torch
 | > Mixed precision: False
 | > Precision: float32
 | > Current device: 0
 | > Num. of GPUs: 1
 | > Num. of CPUs: 24
 | > Num. of Torch Threads: 12
 | > Torch seed: 54321
 | > Torch CUDNN: True
 | > Torch CUDNN deterministic: False
 | > Torch CUDNN benchmark: False
 | > Torch TF32 MatMul: False
 > Start Tensorboard: tensorboard --logdir=/root/tts-output/run-August-14-2023_12+09AM-0000000

 > Model has 84660721 parameters

 > EPOCH: 0/1000
 --> /root/tts-output/run-August-14-2023_12+09AM-0000000

 > TRAINING (2023-08-14 00:09:46) 
/usr/local/lib/python3.10/dist-packages/torch/nn/modules/conv.py:309: UserWarning: Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)
  return F.conv1d(input, weight, bias, self.stride,
/usr/local/lib/python3.10/dist-packages/torch/functional.py:641: UserWarning: stft with return_complex=False is deprecated. In a future pytorch release, stft 

In [3]:
# Vocoder not needed and does not work with VITS model
from TTS.api import Synthesizer

tts = Synthesizer(tts_checkpoint="../TTS/output/run-August-13-2023_06+28PM-0000000/best_model_11229.pth",
                  tts_config_path="../TTS/output/run-August-13-2023_06+28PM-0000000/config.json",
                  vocoder_checkpoint="../../run-August-14-2023_12+09AM-0000000/best_model_486.pth",
                  vocoder_config="../../run-August-14-2023_12+09AM-0000000/config.json"
                 )

#tts = TTS(model_name="/root/tts-output/run-July-26-2023_12+16AM-0000000/best_model_1908.pth", progress_bar=True, gpu=True)

outputs = tts.tts(text="Hello mother. I am Seth's voice clone.")
tts.save_wav(outputs, "output.wav")

 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 > Vocoder Model: hifigan
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:-100
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:

RuntimeError: Given groups=1, weight of size [512, 80, 7], expected input[1, 47872, 11] to have 80 channels, but got 47872 channels instead